# So Your Email Has Been Stolen...

We hear a lot about data breaches, about a company exposing our email addresses or IP addresses. We heave a sigh of relief that it was "just" email addresses or IP addresses. Our passwords and financial data wasn't in danger. This project starts off with a very basic form of OSINT*: what kind of information can attackers find just starting off with the humble email address?

In the previous notebooks, I obtained a list of stolen email addresses, IP addresses, and their geographic locations (latitude and longitude). I also found all their social media accounts.

I now use the email addresses to find out how many data breaches the user has already been in.

In [12]:
#import all here

import numpy as np
import pandas as pd
import requests
import time

In [2]:
#read in master file
df = pd.read_csv("maintable.csv")
df.head(5)

email               ip   latitude  longitude
0     abadisagustin@gmail.com  181.168.120.106 -38.949261 -68.059479
1   Carloselmandril@gmail.com   186.48.125.117 -34.883999 -56.162998
2      cacacasdfa@hotmail.com     186.130.6.73 -34.504719 -58.679520
3  ignaciomortega95@gmail.com   186.18.108.185 -34.687401 -58.563301
4  yerkhomolina1990@gmail.com    181.74.174.95 -33.465000 -70.655998

In [4]:
# it is much easier to work with list of dictionaries than dataframes
rows = df.to_dict('records')
rows

#for testing purposes, just use 5 rows
#rows = df.head(5).to_dict('records')
#rows

[{'email': 'abadisagustin@gmail.com',
  'ip': '181.168.120.106',
  'latitude': -38.94926071166992,
  'longitude': -68.05947875976561},
 {'email': 'Carloselmandril@gmail.com',
  'ip': '186.48.125.117',
  'latitude': -34.88399887084961,
  'longitude': -56.16299819946289},
 {'email': 'cacacasdfa@hotmail.com',
  'ip': '186.130.6.73',
  'latitude': -34.50471878051758,
  'longitude': -58.67951965332031},
 {'email': 'ignaciomortega95@gmail.com',
  'ip': '186.18.108.185',
  'latitude': -34.68740081787109,
  'longitude': -58.56330108642578},
 {'email': 'yerkhomolina1990@gmail.com',
  'ip': '181.74.174.95',
  'latitude': -33.46500015258789,
  'longitude': -70.65599822998047},
 {'email': 'sebas12341992@hotmail.com',
  'ip': '181.49.73.230',
  'latitude': 4.599999904632568,
  'longitude': -74.08332824707031},
 {'email': 'troll@hotmail.com',
  'ip': '190.18.78.110',
  'latitude': -34.66109848022461,
  'longitude': -58.36700057983398},
 {'email': 'j.angulo.valdivia@gmail.com',
  'ip': '190.209.55.16

## Combining with Pwned Data

[HaveIBeenPwned](https://haveibeenpwned.com/API/v2#SingleBreach) is a massive database of all email addresses that have been exposed in data breaches. The [API](https://haveibeenpwned.com/API/v2#SingleBreach) takes a given email address and returns every single incident it has been exposed in. I created a pwned table that lists every single breach.

List of DataFrames:

* df = main table
* pwn = contains data from Have I Been Pwned API
* breaches = all breaches in the database

The common field across tables is the email address or site (name of the breached site)

In [5]:
# call the API for Have I Been Pwned (HIBP) for all breaches

header = {'User-agent':'github.com/fr48 Columbia University Graduate School of Journalism'}
response = requests.get(f'https://haveibeenpwned.com/api/v2/breaches', headers = header)
all_breaches = response.json()

In [6]:
# Make breaches dataframe
breaches = pd.DataFrame(all_breaches)
breaches = breaches[['Name','BreachDate','Domain','PwnCount','DataClasses']]
breaches

Name  BreachDate                 Domain   PwnCount  \
0           000webhost  2015-03-01         000webhost.com   14936670   
1                  126  2012-01-01                126.com    6414191   
2              17Media  2016-04-19               17app.co    4009640   
3                17173  2011-12-28              17173.com    7485802   
4         2844Breaches  2018-02-19                          80115532   
5              2fast4u  2017-12-20             2fast4u.be      17706   
6                500px  2018-07-05              500px.com   14867999   
7                 7k7k  2011-01-01               7k7k.com    9121434   
8                 8fit  2018-07-01               8fit.com   15025407   
9              8tracks  2017-06-27            8tracks.com    7990619   
10           Abandonia  2015-11-01          abandonia.com     776125   
11         AbuseWithUs  2016-07-01           abusewith.us    1372550   
12             AcneOrg  2014-11-25               acne.org     432943   
13               Adapt  2018-11-05               adapt.io    9363740   
14               Adobe  2013-10-04              adobe.com  152445165   
15   AdultFriendFinder  2015-05-21  adultfriendfinder.com    3867997   
16     AdultFanFiction  2018-05-30   adult-fanfiction.org     186082   
17             AerServ  2018-04-01            aerserv.com      66308   
18            AhaShare  2013-05-30           ahashare.com     180468   
19              AIType  2017-12-05             aitype.com   20580060   
20               Aipai  2016-09-27              aipai.com    6496778   
21                 AKP  2016-07-19         akparti.org.tr     917461   
22            Ancestry  2015-11-07           ancestry.com     297806   
23       AndroidForums  2011-10-30      androidforums.com     745355   
24          AntiPublic  2016-12-16                         457962538   
25              Apollo  2018-07-23              apollo.io  125929660   
26            Appartoo  2017-03-25           appartoo.com      49681   
27     ArmyForceOnline  2016-05-18    armyforceonline.com    1531235   
28       AshleyMadison  2015-07-19      ashleymadison.com   30811934   
29            AstroPID  2013-12-19           astropid.com       5788   
..                 ...         ...                    ...        ...   
339             WarInc  2012-07-04          thewarinc.com    1020136   
340           Warframe  2014-11-24           warframe.com     819478   
341            Warmane  2016-12-01            warmane.com    1116256   
342          WeHeartIt  2013-11-03          weheartit.com    8600635   
343         Whitepages  2016-06-27         whitepages.com   11657763   
344              WHMCS  2012-05-21              whmcs.com     134047   
345   WienerBuchereien  2019-06-10                            224119   
346         WifeLovers  2018-10-07         wifelovers.com    1274051   
347            WIIUISO  2015-09-25            wiiuiso.com     458155   
348           WildStar  2015-07-11    wildstar-online.com     738556   
349          Win7Vista  2013-09-03          win7vista.com     202683   
350           Wishbone  2016-08-07            wishbone.io    2247314   
351          WPSandbox  2018-11-04           wpsandbox.io        858   
352                WPT  2014-01-04             wptapl.com     148366   
353                xat  2015-11-04                xat.com    5968783   
354         Xbox360ISO  2015-09-25         xbox360iso.com    1296959   
355         Xbox-Scene  2015-02-01          xboxscene.com     432552   
356           xHamster  2016-11-28           xhamster.com     377377   
357        XPGameSaves  2016-01-01        xpgamesaves.com     890341   
358             XSplit  2013-11-07             xsplit.com    2983472   
359              Yahoo  2012-07-11              yahoo.com     453427   
360             Yandex  2014-09-07       forum.btcsec.com    1186564   
361              Yatra  2013-09-01              yatra.com    5033997   
362              Youku  2016-12-01              youku.com 

### Breaches Table

Each data breach has information such as when it happened and the number of data records stolen. I decided to grab this data from the API so that I can answer questions such as "what's the largest data breach the user was in?" or "What's the most recent data breach the user was in?"

In [13]:
# call the API for Have I Been Pwned (HIBP) for individual accounts

def call_hibp(address):
    header = {'User-agent':'github.com/fr48 Columbia University Graduate School of Journalism'}
    time.sleep(2)
    response = requests.get(f'https://haveibeenpwned.com/api/v2/breachedaccount/{address}', headers = header)
    pwn = response.json()
    return pwn

In [9]:
#what is the table I am working with?
rows

[{'email': 'abadisagustin@gmail.com',
  'ip': '181.168.120.106',
  'latitude': -38.94926071166992,
  'longitude': -68.05947875976561},
 {'email': 'Carloselmandril@gmail.com',
  'ip': '186.48.125.117',
  'latitude': -34.88399887084961,
  'longitude': -56.16299819946289},
 {'email': 'cacacasdfa@hotmail.com',
  'ip': '186.130.6.73',
  'latitude': -34.50471878051758,
  'longitude': -58.67951965332031},
 {'email': 'ignaciomortega95@gmail.com',
  'ip': '186.18.108.185',
  'latitude': -34.68740081787109,
  'longitude': -58.56330108642578},
 {'email': 'yerkhomolina1990@gmail.com',
  'ip': '181.74.174.95',
  'latitude': -33.46500015258789,
  'longitude': -70.65599822998047},
 {'email': 'sebas12341992@hotmail.com',
  'ip': '181.49.73.230',
  'latitude': 4.599999904632568,
  'longitude': -74.08332824707031},
 {'email': 'troll@hotmail.com',
  'ip': '190.18.78.110',
  'latitude': -34.66109848022461,
  'longitude': -58.36700057983398},
 {'email': 'j.angulo.valdivia@gmail.com',
  'ip': '190.209.55.16

## Pwned Table

This is the table that has all the breaches the user has been in, so it is just email address to breach. Much like the earlier profiles table, there is a lot of different rows per user.

In [14]:
pwns = []
for row in rows:
    try:
        records = call_hibp(row['email'])
        for record in records:
            site = {
                'email' : row['email'],
                'site' : record['Name']
            }
            pwns.append(site)
    except:
        print(records)
        pass
pwns

abadisagustin@gmail.com
[{'Name': '8fit', 'Title': '8fit', 'Domain': '8fit.com', 'BreachDate': '2018-07-01', 'AddedDate': '2019-03-21T18:50:00Z', 'ModifiedDate': '2019-03-21T18:50:00Z', 'PwnCount': 15025407, 'Description': 'In July 2018, the health and fitness service <a href="https://8fit.zendesk.com/hc/en-us/articles/360017746394-Notice" target="_blank" rel="noopener">8fit suffered a data breach</a>. The data subsequently appeared for sale on a dark web marketplace in February 2019 and included over 15M unique email addresses alongside names, genders, IP addresses and passwords stored as bcrypt hashes. The data was provided to HIBP by <a href="https://dehashed.com/" target="_blank" rel="noopener">dehashed.com</a>.', 'LogoPath': 'https://haveibeenpwned.com/Content/Images/PwnedLogos/8fit.png', 'DataClasses': ['Email addresses', 'Genders', 'Geographic locations', 'IP addresses', 'Names', 'Passwords'], 'IsVerified': True, 'IsFabricated': False, 'IsSensitive': False, 'IsRetired': False, '

[{'Name': 'R2Games', 'Title': 'R2Games', 'Domain': 'r2games.com', 'BreachDate': '2015-11-01', 'AddedDate': '2016-02-09T12:20:35Z', 'ModifiedDate': '2016-02-09T12:20:35Z', 'PwnCount': 22281337, 'Description': 'In late 2015, the gaming website <a href="https://www.r2games.com" target="_blank" rel="noopener">R2Games</a> was hacked and more than 2.1M personal records disclosed. The vBulletin forum included IP addresses and passwords stored as salted hashes using a weak implementation enabling many to be rapidly cracked. A further 11M accounts were added to "Have I been pwned" in March 2016 and another 9M in July 2016 bringing the total to over 22M.', 'LogoPath': 'https://haveibeenpwned.com/Content/Images/PwnedLogos/R2Games.png', 'DataClasses': ['Email addresses', 'IP addresses', 'Passwords', 'Usernames'], 'IsVerified': True, 'IsFabricated': False, 'IsSensitive': False, 'IsRetired': False, 'IsSpamList': False}]
{'Name': 'R2Games', 'Title': 'R2Games', 'Domain': 'r2games.com', 'BreachDate': '

[{'Name': 'MyHeritage', 'Title': 'MyHeritage', 'Domain': 'myheritage.com', 'BreachDate': '2017-10-26', 'AddedDate': '2019-02-20T21:04:04Z', 'ModifiedDate': '2019-02-20T21:04:04Z', 'PwnCount': 91991358, 'Description': 'In October 2017, the genealogy website <a href="https://blog.myheritage.com/2018/06/myheritage-statement-about-a-cybersecurity-incident/" target="_blank" rel="noopener">MyHeritage suffered a data breach</a>. The incident was reported 7 months later after a security researcher discovered the data and contacted MyHeritage. In total, more than 92M customer records were exposed and included email addresses and salted SHA-1 password hashes. In 2019, <a href="https://www.theregister.co.uk/2019/02/11/620_million_hacked_accounts_dark_web/" target="_blank" rel="noopener">the data appeared listed for sale on a dark web marketplace</a> (along with several other large breaches) and subsequently began circulating more broadly. The data was provided to HIBP by a source who requested it

[{'Name': 'Taringa', 'Title': 'Taringa', 'Domain': 'taringa.net', 'BreachDate': '2017-08-01', 'AddedDate': '2018-04-19T10:11:37Z', 'ModifiedDate': '2018-04-19T10:11:37Z', 'PwnCount': 27971100, 'Description': 'In September 2017, news broke that <a href="https://thehackernews.com/2017/09/taringa-data-breach-hacking.html" target="_blank" rel="noopener">Taringa had suffered a data breach exposing 28 million records</a>. Known as &quot;The Latin American Reddit&quot;, <a href="https://www.taringa.net/posts/taringa/19972402/Un-mensaje-importante-sobre-la-seguridad-de-tu-cuenta.html" target="_blank" rel="noopener">Taringa\'s breach disclosure notice</a> indicated the incident dated back to August that year. The exposed data included usernames, email addresses and weak MD5 hashes of passwords.', 'LogoPath': 'https://haveibeenpwned.com/Content/Images/PwnedLogos/Taringa.png', 'DataClasses': ['Email addresses', 'Passwords', 'Usernames'], 'IsVerified': True, 'IsFabricated': False, 'IsSensitive': F

[{'Name': 'Adobe', 'Title': 'Adobe', 'Domain': 'adobe.com', 'BreachDate': '2013-10-04', 'AddedDate': '2013-12-04T00:00:00Z', 'ModifiedDate': '2013-12-04T00:00:00Z', 'PwnCount': 152445165, 'Description': 'In October 2013, 153 million Adobe accounts were breached with each containing an internal ID, username, email, <em>encrypted</em> password and a password hint in plain text. The password cryptography was poorly done and <a href="http://stricture-group.com/files/adobe-top100.txt" target="_blank" rel="noopener">many were quickly resolved back to plain text</a>. The unencrypted hints also <a href="http://www.troyhunt.com/2013/11/adobe-credentials-and-serious.html" target="_blank" rel="noopener">disclosed much about the passwords</a> adding further to the risk that hundreds of millions of Adobe customers already faced.', 'LogoPath': 'https://haveibeenpwned.com/Content/Images/PwnedLogos/Adobe.png', 'DataClasses': ['Email addresses', 'Password hints', 'Passwords', 'Usernames'], 'IsVerified'

...

[{'Name': 'BabyNames', 'Title': 'Baby Names', 'Domain': 'babynames.com', 'BreachDate': '2008-10-24', 'AddedDate': '2018-10-24T06:27:03Z', 'ModifiedDate': '2018-10-24T06:27:30Z', 'PwnCount': 846742, 'Description': 'In approximately 2008, the site to help parents name their children known as <a href="https://www.babynames.com/" target="_blank" rel="noopener">Baby Names</a> suffered a data breach. The incident exposed 846k email addresses and passwords stored as salted MD5 hashes. When contacted in October 2018, Baby Names advised that &quot;the breach happened at least ten years ago&quot; and that members were notified at the time.', 'LogoPath': 'https://haveibeenpwned.com/Content/Images/PwnedLogos/BabyNames.png', 'DataClasses': ['Email addresses', 'Passwords'], 'IsVerified': True, 'IsFabricated': False, 'IsSensitive': False, 'IsRetired': False, 'IsSpamList': False}, {'Name': 'BusinessAcumen', 'Title': 'Business Acumen Magazine', 'Domain': 'businessacumen.biz', 'BreachDate': '2014-04-25'

[{'Name': 'OnlinerSpambot', 'Title': 'Onliner Spambot', 'Domain': '', 'BreachDate': '2017-08-28', 'AddedDate': '2017-08-29T19:25:56Z', 'ModifiedDate': '2017-08-29T19:25:56Z', 'PwnCount': 711477622, 'Description': 'In August 2017, a spambot by the name of <a href="https://benkowlab.blogspot.com.au/2017/08/from-onliner-spambot-to-millions-of.html" target="_blank" rel="noopener">Onliner Spambot was identified by security researcher Benkow moʞuƎq</a>. The malicious software contained a server-based component located on an IP address in the Netherlands which exposed a large number of files containing personal information. In total, there were 711 million unique email addresses, many of which were also accompanied by corresponding passwords. A full write-up on what data was found is in the blog post titled <a href="https://www.troyhunt.com/inside-the-massive-711-million-record-onliner-spambot-dump" target="_blank" rel="noopener">Inside the Massive 711 Million Record Onliner Spambot Dump</a>.

[{'Name': 'ProgrammingForums', 'Title': 'Programming Forums', 'Domain': 'programmingforums.org', 'BreachDate': '2015-12-01', 'AddedDate': '2017-07-01T16:42:46Z', 'ModifiedDate': '2017-07-01T16:42:46Z', 'PwnCount': 707432, 'Description': 'In approximately late 2015, the programming forum at <a href="http://www.programmingforums.org/" target="_blank" rel="noopener">programmingforums.org</a> suffered a data breach resulting in the exposure of 707k unique user records. The data contained email and IP addresses, usernames and salted MD5 hashes of passwords. The site was previously reported as compromised on the <a href="https://vigilante.pw/" target="_blank" rel="noopener">Vigilante.pw</a> breached database directory.', 'LogoPath': 'https://haveibeenpwned.com/Content/Images/PwnedLogos/ProgrammingForums.png', 'DataClasses': ['Email addresses', 'IP addresses', 'Passwords', 'Usernames'], 'IsVerified': True, 'IsFabricated': False, 'IsSensitive': False, 'IsRetired': False, 'IsSpamList': False}]


[{'Name': 'Dropbox', 'Title': 'Dropbox', 'Domain': 'dropbox.com', 'BreachDate': '2012-07-01', 'AddedDate': '2016-08-31T00:19:19Z', 'ModifiedDate': '2016-08-31T00:19:19Z', 'PwnCount': 68648009, 'Description': 'In mid-2012, Dropbox suffered a data breach which exposed the stored credentials of tens of millions of their customers. In August 2016, <a href="https://motherboard.vice.com/read/dropbox-forces-password-resets-after-user-credentials-exposed" target="_blank" rel="noopener">they forced password resets for customers they believed may be at risk</a>. A large volume of data totalling over 68 million records <a href="https://motherboard.vice.com/read/hackers-stole-over-60-million-dropbox-accounts" target="_blank" rel="noopener">was subsequently traded online</a> and included email addresses and salted hashes of passwords (half of them SHA1, half of them bcrypt).', 'LogoPath': 'https://haveibeenpwned.com/Content/Images/PwnedLogos/Dropbox.png', 'DataClasses': ['Email addresses', 'Passwor

[{'email': 'abadisagustin@gmail.com', 'site': '8fit'},
 {'email': 'troll@hotmail.com', 'site': '000webhost'},
 {'email': 'troll@hotmail.com', 'site': '500px'},
 {'email': 'troll@hotmail.com', 'site': 'AbuseWithUs'},
 {'email': 'troll@hotmail.com', 'site': 'Adobe'},
 {'email': 'troll@hotmail.com', 'site': 'ArmyForceOnline'},
 {'email': 'troll@hotmail.com', 'site': 'Bitly'},
 {'email': 'troll@hotmail.com', 'site': 'CrackingForum'},
 {'email': 'troll@hotmail.com', 'site': 'CrossFire'},
 {'email': 'troll@hotmail.com', 'site': 'Dailymotion'},
 {'email': 'troll@hotmail.com', 'site': 'DataAndLeads'},
 {'email': 'troll@hotmail.com', 'site': 'Disqus'},
 {'email': 'troll@hotmail.com', 'site': 'Dropbox'},
 {'email': 'troll@hotmail.com', 'site': 'Dubsmash'},
 {'email': 'troll@hotmail.com', 'site': 'Edmodo'},
 {'email': 'troll@hotmail.com', 'site': 'EverybodyEdits'},
 {'email': 'troll@hotmail.com', 'site': 'Evony'},
 {'email': 'troll@hotmail.com', 'site': 'Exactis'},
 {'email': 'troll@hotmail.com',

In [15]:
# Make breaches dataframe
pwned = pd.DataFrame(pwns)
pwned

email                     site
0         abadisagustin@gmail.com                     8fit
1               troll@hotmail.com               000webhost
2               troll@hotmail.com                    500px
3               troll@hotmail.com              AbuseWithUs
4               troll@hotmail.com                    Adobe
5               troll@hotmail.com          ArmyForceOnline
6               troll@hotmail.com                    Bitly
7               troll@hotmail.com            CrackingForum
8               troll@hotmail.com                CrossFire
9               troll@hotmail.com              Dailymotion
10              troll@hotmail.com             DataAndLeads
11              troll@hotmail.com                   Disqus
12              troll@hotmail.com                  Dropbox
13              troll@hotmail.com                 Dubsmash
14              troll@hotmail.com                   Edmodo
15              troll@hotmail.com           EverybodyEdits
16              troll@hotmail.com                    Evony
17              troll@hotmail.com                  Exactis
18              troll@hotmail.com             GamerzPlanet
19              troll@hotmail.com                  Playgar
20              troll@hotmail.com          HeroesOfNewerth
21              troll@hotmail.com                     HLTV
22              troll@hotmail.com                    iMesh
23              troll@hotmail.com                    imgur
24              troll@hotmail.com              Kickstarter
25              troll@hotmail.com                     Leet
26              troll@hotmail.com                 Lifeboat
27              troll@hotmail.com                 LinkedIn
28              troll@hotmail.com  ModernBusinessSolutions
29              troll@hotmail.com                     MPGH
...                           ...                      ...
1848        tiepleser@hotmail.com                 Creative
1849        tiepleser@hotmail.com                  Digimon
1850        tiepleser@hotmail.com           OnlinerSpambot
1851        tiepleser@hotmail.com         SocialEngineered
1852        tiepleser@hotmail.com                  Solomid
1853           ucgmusou@gmail.com                    Adobe
1854   referateonlineus@yahoo.com                Coachella
1855                  guira@uv.es                  Dropbox
1856                  guira@uv.es                 LinkedIn
1857                  guira@uv.es                  MySpace
1858                  guira@uv.es                Ticketfly
1859       julia.kuligowski@uv.es                  Dropbox
1860       julia.kuligowski@uv.es                     MDPI
1861            weijkkgew@sina.cn                BabyNames
1862            weijkkgew@sina.cn           BusinessAcumen
1863            weijkkgew@sina.cn                 Creative
1864            weijkkgew@sina.cn                  Digimon
1865            weijkkgew@sina.cn                  Kimsufi
1866            weijkkgew@sina.cn             Mac-Torrents
1867            weijkkgew@sina.cn                     MPGH
1868            weijkkgew@sina.cn           OnlinerSpambot
1869     m.rotival@imperial.ac.uk           OnlinerSpambot
1870       pfem.bioinfo@gmail.com                  Dropbox
1871  dctormorguls777@hotmail.com        ProgrammingForums
1872         fatma.njeh@gmail.com              Dailymotion
1873         dgemperline@wisc.edu                   Apollo
1874         dgemperline@wisc.edu                Ticketfly
1875         dgemperline@wisc.edu          VerificationsIO
1876   xiaoliang.sun@univie.ac.at                  Dropbox
1877   xiaoliang.sun@univie.ac.at                     MDPI

[1878 rows x 2 columns]

## Write to file

In [16]:
#write to file
breaches.to_csv('breaches.csv', index=0)

In [17]:
pwned.to_csv('pwned.csv', index=0)

### Path Not Taken \[2\]

I was thinking about how to create the pwned table, and we were thinking about working with the different DataClasses. Keeping the code (which works) for posterity

```
pwns =[]
for row in rows:
    incidents = {}
    records = call_hibp(row['email'])
    incidents = {
        'email' : row['email']
    }
    for record in records['DataClasses']:
        info.update({record:'Y'})
        sites = {
            'email' : records['email'],
            'social': record
        }
        prof.append(sites)
    rep.append(info)
```